In [3]:
import numpy as np
import apogee.tools.read as apread
from matplotlib import pyplot as plt
import pandas as pd
import csv
from apogee.tools import bitmask
import math
from astropy.io import fits
import os.path
from pathlib import Path

In [4]:
# Set a timer to calculate the amount of time it takes for the main routine to run
def timer():
    print('into the abyss!')
    start = time.time()
    end = time.time()
    elapsed = end - start
    time = round(elaped,3)
    return time

In [5]:
#Calculate R-Values for given ranges
def calcR(x,pm):
    ccfCenter = max(x)
    primary = np.where(x == ccfCenter)
    peak_loc = primary[0][0]
    if peak_loc < pm: 
        pm = peak_loc
    if peak_loc > 401 - pm:
        pm = 401 - peak_loc
    if peak_loc == 0:
        r = 1000
        return r 
    endpoint = peak_loc+pm
    startpoint= peak_loc-pm
    Mirror = (x[peak_loc:endpoint])[::-1]
    sigmaA = np.sqrt(1.0 / (2.0 * len(Mirror)) * np.sum((x[startpoint:peak_loc] - Mirror)**2))
    r = np.max(x) / (np.sqrt(2.0) * sigmaA)
    return r

In [6]:
#Calculate the bisector points for a CCF (uses 4 points)
def bisector(xccf,yccf):
    height = max(yccf) - min(yccf)
    slices = height/4.0
    bounds = np.arange(min(yccf),height,slices)
    if len(bounds) != 0:
        z1 = (bounds[0] + bounds[1])/2.0
        z2 = (bounds[1] + bounds[2])/2.0
        z3 = (bounds[2] + bounds[3])/2.0
        z4 = (bounds[3] + bounds[4])/2.0
        y_bisector = np.array([z1,z2,z3,z4])

        x_bisector = []
        x0 = []
        x1 = []
        x2 = []
        x3 = []
        for i in range(len(yccf)):
            if yccf[i] <= bounds[4] and yccf[i] > bounds[3]:
                x0.append(xccf[i])
        x_0 = (np.mean(x0))
        x_bisector.append(x_0)

        i = 0
        for i in range(len(yccf)):
            if yccf[i] <= bounds[3] and yccf[i] >= bounds[2]:
                x1.append(xccf[i])
        x_1=(np.mean(x1))
        x_bisector.append(x_1)

        i = 0
        for i in range(len(yccf)):
            if yccf[i] <= bounds[2] and yccf[i] >= bounds[1]:
                x2.append(xccf[i])
        x_2=(np.mean(x2))
        x_bisector.append(x_2)

        i = 0
        for i in range(len(yccf)):
            if yccf[i] <= bounds[1] and yccf[i] >= bounds[0]:
                x3.append(xccf[i])
        x_3=(np.mean(x3))
        x_bisector.append(x_3)

        bisector_pts = np.vstack([x_bisector,y_bisector])
        #print(bisector_pts)
        return(bisector_pts)

In [7]:
def xrange(x_bisector):
    #print(x_bisector)
    xr = max(x_bisector) - min(x_bisector)
    return xr

In [8]:
#Calculate the R-ratios for the likely_binary function
def r_ratio(r51,r151,r101):
        #print(r51, r101,r151)
        r1_ratio = r151/r101
        r2_ratio = r101/r51
        R1_ratio = math.log10(r1_ratio)
        R2_ratio = math.log10(r2_ratio)
        ratios = [round(R1_ratio,3),round(R2_ratio,3)]
        return ratios

def idSB2s(R1_ratio, R2_ratio,r51,r151,r101,xr): # cuts to identify SB2s from Kevin's IDL Routine
    min_r51 = r51
    min_r101 = r101
    min_r151 = r151
    r1_ratio = R1_ratio
    r2_ratio = R2_ratio
    max_xr = xr
    
    likely_sb2s = np.where((math.log10(r1_ratio) > 0.06 and (math.log10(r1_ratio) < 0.13 and 
                            math.log10(min_r101) < 0.83)) or (math.log10(r2_ratio) > 0.05 and 
                            math.log10(r2_ratio) < 0.02 and math.log10(min_r51) < 0.83) and
                            math.log10(min_r51) > 0.25 and math.log10(min_r101) > 0.22 and
                            math.log10(peak_401) > -0.5 and math.log10(max_xr) < 2.3 and 
                            math.log10(max_xr) > 0.7
                          )
    return likely_sb2s

In [9]:
# Read in DR14 allStar File

allStarDR14 = apread.allStar(rmcommissioning=False,main=False,ak=True,akvers='targ',adddist=False)

locationIDs = allStarDR14['LOCATION_ID']
apogeeIDs = allStarDR14['APOGEE_ID']
apogeeIDs = [s.decode('utf-8') for s in apogeeIDs]

In [12]:
#Begin output for stats of all stars in DR14
import time #For the timer function
start = time.time()
with open('DR14_Stat_Catalog_Complete.csv','w') as output:
    column = ['Location_ID','Apogee_ID','Visit','SNR','xRng','R51','R101','R151','R151/101','R101/51',]
    writer = csv.DictWriter(output,delimiter='\t',fieldnames=column)
    writer.writeheader()
    miss_apogeeID = []
    miss_locationID = []
    #for i in range(len(locationIDs)):
    #for i in range(129172,129175):
    for i in range(0,129173):
        locationID = locationIDs[i]
        apogeeID = apogeeIDs[i]
        print(i,locationID,apogeeID)
        my_file = Path('/Volumes/coveydata/APOGEE_Spectra/APOGEE2_DR14/dr14/apogee/spectro/redux/r8/stars/apo25m/'+str(locationID)+'/'+'apStar-r8-'+str(apogeeID)+'.fits')
        try: 
            path = '/Volumes/coveydata/APOGEE_Spectra/APOGEE2_DR14/dr14/apogee/spectro/redux/r8/stars/apo25m/'+str(locationID)+'/'+'apStar-r8-'+str(apogeeID)+'.fits'
            data = fits.open(path)
    
        except OSError:
            print('enter')
            miss_apogeeID.append(apogeeID)
            miss_locationID.append(locationID)
            pass
            #path = '/Volumes/coveydata/APOGEE_Spectra/APOGEE2_DR14/dr14/apogee/spectro/redux/r8/stars/apo25m/'+str(locationID)+'/'+'apStarC-r8-'+str(apogeeID)+'.fits'
        point = data[9]
        xccf = point.data[0][32]
        CCF = point.data[0][27]
        HDU0 = fits.getheader(path,0)
        nvisits = HDU0['NVISITS']
        for visit in range(0,nvisits):
            ccf = CCF[visit+2]
            snr = HDU0['SNRVIS'+str(visit+2)]
            if snr >= 10: # Set the condition for stars to have >= 10 snr
                nonzeroes = np.count_nonzero(ccf) # This condition is meant to eliminate visits that are empty
                if nonzeroes >= 1:
                    bs_pt = bisector(xccf, ccf)
                    x_range = xrange(bs_pt[0])
                    R151 = calcR(ccf,75)
                    R101 = calcR(ccf,50)
                    R51 = calcR(ccf,25)
                    Ratios = r_ratio(R51,R151,R101)
                    r1 = Ratios[0]
                    r2 = Ratios[1]
                    writer.writerow({'Location_ID':locationID,'Apogee_ID':apogeeID,'Visit':visit,'SNR':snr,'xRng':round(x_range,3),
                                             'R51':round(R51,3),'R101':round(R101,3),'R151':round(R151,3),'R151/101':r1,'R101/51':r2})
                    else:
                        pass
    end = time.time()
    elapsed = end - start
    print(round(elapsed,3))

0 5046 2M00000002+7417074
1 5071 2M00000019-1924498
2 4264 2M00000032+5737103
3 4424 2M00000032+5737103
4 4264 2M00000068+5710233
5 4591 2M00000211+6327470
6 4264 2M00000222+5625359
7 4548 2M00000233+1452324
8 4424 2M00000317+5821383
9 4424 2M00000446+5854329
10 5071 2M00000523-1937381
11 4548 2M00000535+1504343
12 5045 2M00000546+6152107
13 5046 2M00000662+7528598
14 4591 2M00000797+6436119
15 5047 2M00000799+7939442
16 4264 2M00000818+5634264
17 4120 2M00000866+7122144
18 5045 2M00000943+6254542
19 5045 2M00001045+6126148
20 5045 2M00001071+6258172
21 4591 2M00001104+6348085
22 5045 2M00001199+6114138
23 5071 2M00001210-1903382
24 5071 2M00001217-1949306
25 4264 2M00001242+5524391
26 4424 2M00001296+5851378
27 4264 2M00001328+5725563
28 5071 2M00001362-1913042
29 5045 2M00001508+6229364
30 4548 2M00001616+1606151
31 5047 2M00001638+7924440
32 4264 2M00001653+5540107
33 4424 2M00001687+5903034
34 4120 2M00001701+7052395
35 5045 2M00001717+6147500
36 5045 2M00001719+6221324
37 4424 2M0

297 5047 2M00014989+8003031
298 5046 2M00015007+7323169
299 4590 2M00015064+0023161
300 4590 2M00015091+0131134
301 4548 2M00015093+1526161
302 4548 2M00015102+1650371
303 4287 2M00015205+7315215
304 5046 2M00015205+7315215
305 4424 2M00015243+5930120
306 4548 2M00015250+1551269
307 4264 2M00015271+5559366
308 4264 2M00015324+5634361
309 4590 2M00015342+0114481
310 4591 2M00015350+6459174
311 4264 2M00015524+5536322
312 4120 2M00015591+6949468
313 4590 2M00015592+0027057
314 4424 2M00015741+5918131
315 4287 2M00015747+7336048
316 5046 2M00015812+7425157
317 4548 2M00015855+1719569
318 4548 2M00015887+1639429
319 4590 2M00015905+0052119
320 4264 2M00015923+5551011
321 4287 2M00015949+7416589
322 4548 2M00015950+1632062
323 4548 2M00015966+1627449
324 4424 2M00020080+5817510
325 5045 2M00020308+6234023
326 4287 2M00020346+7513405
327 4264 2M00020348+5651433
328 4264 2M00020371+5645019
329 4548 2M00020489+1502157
330 4424 2M00020505+5855219
331 5047 2M00020526+8013092
332 4591 2M00020564+

592 4424 2M00033334+5917055
593 5052 2M00033341+6847231
594 4590 2M00033371+0200331
595 4591 2M00033477+6329257
596 4424 2M00033511+5930095
597 4548 2M00033563+1521317
598 4287 2M00033618+7445199
599 5047 2M00033629+7917522
600 4120 2M00033808+7018217
601 4590 2M00033817+0020226
602 5052 2M00033901+6911339
603 4287 2M00033942+7335499
604 5046 2M00033942+7335499
605 4548 2M00034057+1658434
606 5052 2M00034082+6852258
607 5052 2M00034087+6838207
608 4120 2M00034088+7043002
609 4424 2M00034090+5812525
610 5046 2M00034104+7602261
611 4591 2M00034140+6322213
612 4287 2M00034151+7558168
613 4264 2M00034169+5658292
614 4287 2M00034210+7312343
615 4548 2M00034257+1605111
616 4424 2M00034437+5852377
617 4120 2M00034443+7141117
618 5046 2M00034514+7433521
619 5045 2M00034578+6150008
620 4120 2M00034596+7107075
621 4287 2M00034612+7434320
622 5046 2M00034612+7434320
623 4287 2M00034648+7524537
624 5046 2M00034648+7524537
625 4120 2M00034672+7001400
626 5045 2M00034722+6214207
627 5045 2M00034743+

886 4590 2M00055969-0030062
887 5052 2M00055986+6850184
888 4287 2M00060018+7321297
889 4120 2M00060064+7001540
890 4590 2M00060072+0033278
891 4120 2M00060087+7123370
892 5052 2M00060114+6929392
893 4120 2M00060224+7142202
894 4590 2M00060310+0158204
895 4287 2M00060350+7442543
896 4590 2M00060369+0104479
897 4120 2M00060394+7014587
898 4287 2M00060411+7345557
899 5052 2M00060440+6845371
900 4120 2M00060520+7035327
901 4590 2M00060564+0025121
902 5046 2M00060682+7412011
903 4424 2M00060944+5733429
904 4590 2M00060971+0120321
905 4287 2M00060972+7516165
906 5046 2M00060972+7516165
907 4287 2M00060975+7517457
908 5052 2M00061048+6914423
909 5052 2M00061093+6833151
910 4120 2M00061198+7143163
911 4590 2M00061237+0101599
912 5046 2M00061328+7512193
913 4120 2M00061363+7133365
914 4287 2M00061380+7348435
915 5046 2M00061380+7348435
916 4287 2M00061383+7537210
917 5046 2M00061383+7537210
918 4590 2M00061415+0127198
919 4287 2M00061435+7539398
920 4590 2M00061555+0037518
921 5052 2M00061689+

1174 4590 2M00080598+0055455
1175 4120 2M00080626+7059003
1176 4120 2M00080626+7151555
1177 4590 2M00080678+0057034
1178 4287 2M00080694+7412039
1179 4287 2M00080765+7513454
1180 5052 2M00080797+6859050
1181 5052 2M00080849+6818353
1182 4120 2M00080855+7134126
1183 4424 2M00080940+5909219
1184 4590 2M00080965+0054565
1185 4120 2M00080998+7109340
1186 4590 2M00081030+0048200
1187 5052 2M00081099+6817426
1188 4120 2M00081118+7034249
1189 4287 2M00081127+7416348
1190 5046 2M00081179+7533076
1191 4590 2M00081209+0035026
1192 5046 2M00081271+7316405
1193 4424 2M00081288+5825054
1194 4424 2M00081292+5800187
1195 5052 2M00081296+6844058
1196 4424 2M00081326+5836110
1197 4590 2M00081390+0152211
1198 4424 2M00081458+5826219
1199 4120 2M00081496+7008599
1200 5046 2M00081510+7510241
1201 4590 2M00081555+0040277
1202 5052 2M00081596+6811453
1203 5052 2M00081597+6745499
1204 4120 2M00081620+6938364
1205 4287 2M00081745+7353086
1206 4424 2M00081782+5847060
1207 4287 2M00081787+7338185
1208 5052 2M00

...

128074 4218 2M12251747+1450078
128075 4125 2M12251761+0041123
128076 4125 2M12251788-0026421
128077 4218 2M12251791+1529398
128078 4501 2M12251805+5631093
128079 2118 2M12251841+4535405
128080 2181 2M12251841+4535405
128081 4501 2M12251852+5751452
128082 4218 2M12251862+1309342
128083 4501 2M12251866+5557536
128084 2116 2M12251930+4345278
128085 4513 2M12251932-0105000
128086 4216 2M12251999+2531521
128087 2181 2M12252038+4522101
128088 4216 2M12252071+2642103
128089 4125 2M12252074-0111585
128090 4216 2M12252076+2517082
128091 4501 2M12252079+5744598
128092 4216 2M12252133+2603017
128093 4216 2M12252193+2602254
128094 4218 2M12252238+1507276
128095 4216 2M12252278+2544517
128096 4501 2M12252400+5806229
128097 4216 2M12252404+2659467
128098 4501 2M12252405+5647383
128099 4125 2M12252442+0008134
128100 4216 2M12252510+2700023
128101 2118 2M12252564+4723153
128102 4216 2M12252610+2600393
128103 4216 2M12252652+2523219
128104 2118 2M12252655+4605548
128105 2181 2M12252655+4605548
128106 4

128339 4218 2M12263613+1507028
128340 2118 2M12263631+4735168
128341 4501 2M12263647+5643386
128342 4218 2M12263649+1437590
128343 4216 2M12263724+2634126
128344 4218 2M12263754+1429192
128345 4125 2M12263810+0010222
128346 2118 2M12263854+4716245
128347 4125 2M12263867-0006125
128348 2116 2M12263899+4440190
128349 2181 2M12263899+4440190
128350 4125 2M12263910-0013025
128351 4216 2M12263913+2505546
128352 4125 2M12263922+0006254
128353 2118 2M12263958+4627345
128354 2181 2M12263958+4627345
128355 4216 2M12263985+2602219
128356 4125 2M12263999+0004024
128357 4216 2M12264013+2640482
128358 4216 2M12264027+2718434
128359 4216 2M12264037+2722178
128360 4501 2M12264051+5610333
128361 4513 2M12264128-0320574
128362 4125 2M12264170+0014380
128363 4216 2M12264182+2443262
128364 4125 2M12264217+0018589
128365 4501 2M12264220+5712113
128366 4125 2M12264226+0008064
128367 4216 2M12264232+2608591
128368 2118 2M12264239+4514079
128369 2118 2M12264264+4506326
128370 2181 2M12264264+4506326
128371 4

128604 4513 2M12275759-0106150
128605 4513 2M12275808-0202492
128606 4218 2M12275818+1532125
128607 4216 2M12275922+2704194
128608 4501 2M12275942+5650560
128609 4216 2M12275945+2550328
128610 4501 2M12275976+5548068
128611 4501 2M12275979+5812540
128612 4218 2M12275993+1443115
128613 2181 2M12280039+4452266
128614 4501 2M12280145+5744554
128615 2118 2M12280180+4607274
128616 2181 2M12280180+4607274
128617 4513 2M12280185-0105301
128618 4216 2M12280185+2706333
128619 2181 2M12280239+4457562
128620 4216 2M12280291+2529425
128621 4513 2M12280489-0148256
128622 2118 2M12280491+4723201
128623 4216 2M12280507+2623120
128624 2118 2M12280609+4528534
128625 2181 2M12280609+4528534
128626 2118 2M12280636+4602295
128627 2181 2M12280636+4602295
128628 2181 2M12280659+4450414
128629 4216 2M12280700+2536059
128630 4501 2M12280717+5736302
128631 4218 2M12280797+1340080
128632 2118 2M12280802+4515102
128633 2181 2M12280802+4515102
128634 4513 2M12280808-0311531
128635 4216 2M12280826+2534428
128636 4

128870 4513 2M12300057-0150499
128871 4218 2M12300252+1322152
128872 4216 2M12300256+2640242
128873 4513 2M12300298-0216206
128874 4513 2M12300299-0113324
128875 4501 2M12300304+5708161
128876 4513 2M12300331-0213396
128877 4513 2M12300359-0123293
128878 4501 2M12300429+5619422
128879 4218 2M12300433+1444417
128880 2181 2M12300436+4527355
128881 4216 2M12300671+2509013
128882 2181 2M12300787+4447516
128883 4513 2M12300810-0117401
128884 2181 2M12300822+4422539
128885 4513 2M12300914-0142077
128886 4218 2M12300976+1417537
128887 4501 2M12301148+5555229
128888 4218 2M12301231+1401481
128889 4216 2M12301232+2632015
128890 2118 2M12301291+4624058
128891 2181 2M12301291+4624058
128892 4216 2M12301420+2642069
128893 2181 2M12301463+4401090
128894 4501 2M12301508+5750591
128895 4513 2M12301551-0154190
128896 4513 2M12301580-0127297
128897 4218 2M12301597+1358482
128898 4513 2M12301624-0148594
128899 2118 2M12301697+4615026
128900 2181 2M12301697+4615026
128901 4501 2M12301750+5706592
128902 4

129136 2181 2M12361247+4540594
129137 2151 2M12361688+4526217
129138 2181 2M12361688+4526217
129139 2151 2M12361740+4452036
129140 2181 2M12361740+4452036
129141 2151 2M12362106+4608334
129142 2151 2M12362421+4618037
129143 2151 2M12362831+4647021
129144 2151 2M12362940+4621247
129145 2151 2M12363097+4656035
129146 2151 2M12363373+4506108
129147 2181 2M12363373+4506108
129148 2181 2M12363477+4521537
129149 2151 2M12364317+4605130
129150 2151 2M12364388+4531139
129151 2151 2M12364520+4449495
129152 2151 2M12364724+4502213
129153 2151 2M12364833+4636490
129154 2151 2M12364850+4505469
129155 2151 2M12365154+4542064
129156 2151 2M12370795+4630516
129157 2151 2M12372671+4514409
129158 2151 2M12372844+4549265
129159 2151 2M12373499+4600463
129160 2151 2M12373636+4610405
129161 2151 2M12373701+4521293
129162 2151 2M12373781+4539492
129163 2151 2M12374105+4657353
129164 2151 2M12374122+4613284
129165 2151 2M12374478+4451158
129166 2151 2M12374932+4425136
129167 2151 2M12375479+4517042
129168 4

### Read the 129,172 Stars that were passed through the routine above and try to pass them through the binary where condition.


In [28]:
# Read in the file and find how many are SB2s. 
stats = pd.read_csv('DR14_Stats_Catalog.csv',delimiter='\t')
FieldID = stats['Location_ID']
TwoMassID = stats['Apogee_ID']
Star_Visit = stats['Visit']
logR1 = stats['R151/101']
logR2 = stats['R101/51']
R51s = stats['R51']
R101s = stats['R101']
R151s = stats['R151']
xr_value = stats['xRng']
print(len(R151s))

477033


In [ ]:
ptl.plot()

In [31]:
# Read in the file and find how many are SB2s. 
with open('DR14_SB2_Catalog.csv','w') as files:
    column = ['Location_ID','Apogee_ID']
    writer = csv.DictWriter(files,delimiter='\t',fieldnames=column)
    writer.writeheader()
    i = 0
    r1 = []
    r2 = []
    r51 = []
    r101 = []
    r151 = []
    xranges = []
    SB2 = []
    for i in range(len(FieldID)):
        if Star_Visit[i] == Star_Visit[i]:
            r1.append(logR1[i])
            r2.append(logR2[i])
            r51.append(R51s[i])
            r101.append(R101s[i])
            r151.append(R151s[i])
            xranges.append(xr_value[i])
        likely_binary = idSB2s(r1, r2,r51,r151,r101,xranges)
        index_locID = FieldID[likely_binary]
        index_apoID = TwoMassID[likely_binary]
        SB2.append([index_locID,index_apoID])
        writer.writerow({'Location_ID': SB2[0] ,'Apogee_ID':SB2[1]})

TypeError: must be real number, not list